# ETL

For my first individual project at Henry, an ETL (Extract, Transform, Load) task is required in order to load all our data into a reliable database without any inconsistencies.

## Pipeline:
1. Extract and Transformation done with pandas, and these are some point considered during this task:
    * All data was  loaded into a google drive folder, in order to avoid any git issue due to the large memory size uploading to git, also to avoid memory limitations at render (only 512 MB)
    * There are no records to withdraw but only the fields indicated in Henry's project guidance. It is recomendable to wait until the EDA work is done for evaluation
    * There will be some funtion to perform data imputation with "values".

2. Then all data will be loaded to a Mongo Data Base.
    * The Data Base choosen is MongoAtlas since it offers an a free usage for little personal projects and cloud base deployment. Having a data base in the cloud will allow the deployment at render to use this database with simple pymongo queriess

### Why Mongo?
At first glance, there are a few fields that contain arrays (lists) with dictionaries. Mongo allow working with this king od structures. To understand better mongo objects: instead of working with tables, columns (a.k.a. fields), and rows, in MongoDB we work with collections (analogy to tables), documents (rows), and fields (also fields in tabular data ;) ).. but, how a colletion looks like? .. like this:

![Collection](images\crud-annotated-collection.bakedsvg.svg)

Import all resources, see that pymongo is included. But have in mind this is only the driver that enable perform CRUD operation in a Mongo database

In [2]:
# Import dependencies
import pandas as pd
import numpy as np
import pymongo
import openpyxl
import ast
from json import loads, dumps
from datetime import datetime

In [25]:
# Load data set from local directory. You can download the files from my google drive if you want to reproduce this ETL.
df = pd.read_excel("Data/movies_dataset.xlsx", converters={'release_date': pd.to_datetime})

In [26]:
df.head(2)

adult                              belongs_to_collection    budget  \
0  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1  False                                                NaN  65000000   

                                              genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
1  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   

                               homepage    id    imdb_id original_language  \
0  http://toystory.disney.com/toy-story   862  tt0114709                en   
1                                   NaN  8844  tt0113497                en   

  original_title                                           overview  ...  \
0      Toy Story  Led by Woody, Andy's toys live happily in his ...  ...   
1        Jumanji  When siblings Judy and Peter discover an encha...  ...   

  release_date      revenue runtime  \
0   1995-10-30  373554033.0    81.0   
1   1995-12-15  262797249.0   104.0   

                                    spoken_languages    status  \
0           [{'iso_639_1': 'en', 'name': 'English'}]  Released   
1  [{'iso_639_1': 'en', 'name': 'English'}, {'iso...  Released   

                                     tagline      title video vote_average  \
0                                        NaN  Toy Story   0.0          7.7   
1  Roll the dice and unleash the excitement!    Jumanji   0.0          6.9   

  vote_count  
0     5415.0  
1     2413.0  

[2 rows x 24 columns]

In [27]:
df.dtypes

adult                            object
belongs_to_collection            object
budget                           object
genres                           object
homepage                         object
id                               object
imdb_id                          object
original_language                object
original_title                   object
overview                         object
popularity                       object
poster_path                      object
production_companies             object
production_countries             object
release_date             datetime64[ns]
revenue                         float64
runtime                         float64
spoken_languages                 object
status                           object
tagline                          object
title                            object
video                           float64
vote_average                    float64
vote_count                      float64
dtype: object

# Data Wrangling

Dealing with missing values and dtypes

In [28]:
# Here is listed the percentage of missing data for each field (remember, a.k.a. column)
round(df.isna().sum() / df.shape[0]  * 100, 2)

adult                     0.00
belongs_to_collection    90.12
budget                    0.00
genres                    0.00
homepage                 82.88
id                        0.00
imdb_id                   0.04
original_language         0.02
original_title            0.00
overview                  2.11
popularity                0.01
poster_path               0.85
production_companies      0.01
production_countries      0.01
release_date              0.19
revenue                   0.01
runtime                   0.58
spoken_languages          0.01
status                    0.19
tagline                  55.11
title                     0.01
video                     0.01
vote_average              0.01
vote_count                0.01
dtype: float64

As we've seen at our Data Frame, we can find few fields with list, such as genres.. lets take a look at single row of this field and figure out what datatype is.

In [29]:
df['genres'][0], type(df['genres'][0])

("[{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}]",
 str)

# Catching Arrays

Those objects that looks like a list with dictionaries are simple strings (it seems that's due to .read_excel() method, but it is fine! I prefer this to proceed with unnotified dtype changes as excel does), and would be more suitable working with appropiate datatype in order to call all list and dictionary methods to perform data manipulation

ast.literal_eval help us to take an string as literal what it is in the string. ast.literal parse all the grammar and return the object. Try it

In [30]:
# Here a simple example parsing an a string "['cat', 'dog']", look up! it is a string, not a list of strings
ast.literal_eval("['cat', 'dog']")

['cat', 'dog']

And by calling .apply() method we can perform this sooouseful method on each row in the panda series

In [31]:
df.genres.apply(ast.literal_eval)[0], type(df.genres.apply(ast.literal_eval)[0])

([{'id': 16, 'name': 'Animation'},
  {'id': 35, 'name': 'Comedy'},
  {'id': 10751, 'name': 'Family'}],
 list)

And these are the fields that I see with this kind of structure, and we are going to find out why there are few missing data in "belongs_to_collection"

In [32]:
nested_data_columns = ['belongs_to_collection','genres','production_companies', 'production_countries', 'spoken_languages']
df.loc[:,nested_data_columns].isna().sum()

belongs_to_collection    40972
genres                       0
production_companies         3
production_countries         3
spoken_languages             6
dtype: int64

# Data Manipulation!

Let's create a copy to run some test without having to read those csv and excel files again.

In [33]:
df_copy = df.copy()

Taking a look at dtypes again, just to refresh..

In [34]:
df_copy.dtypes

adult                            object
belongs_to_collection            object
budget                           object
genres                           object
homepage                         object
id                               object
imdb_id                          object
original_language                object
original_title                   object
overview                         object
popularity                       object
poster_path                      object
production_companies             object
production_countries             object
release_date             datetime64[ns]
revenue                         float64
runtime                         float64
spoken_languages                 object
status                           object
tagline                          object
title                            object
video                           float64
vote_average                    float64
vote_count                      float64
dtype: object

In [35]:
# Missing data
df_copy.isna().sum()

adult                        0
belongs_to_collection    40972
budget                       0
genres                       0
homepage                 37684
id                           0
imdb_id                     17
original_language           11
original_title               0
overview                   959
popularity                   5
poster_path                386
production_companies         3
production_countries         3
release_date                87
revenue                      6
runtime                    263
spoken_languages             6
status                      87
tagline                  25055
title                        6
video                        6
vote_average                 6
vote_count                   6
dtype: int64

### Dropping Fields
Let's begin with the easiest ones: dropping fields! 

In [36]:
df_copy.drop(['video', 'imdb_id', 'adult', 'original_title', 'poster_path', 'homepage'], axis = 1, inplace=True)

### Filling null values on "revenue" and "budget" and other fields (time stamp) with default values

According to henry's guidance project, We should fill numeric missing data with zeros, but I'll leverage this taks to handle the time stamp fields

In [37]:
# How many rows are missing in the field "release_date"?
df_copy["release_date"].isna().sum()

87

Check out the bellow function

In [38]:
def defaults_filler(dataFrame: pd.DataFrame, columns_names: list):
    """
    This is an ad-hoc function for this data wrangling.
    


    Parameters:
        dataFrame (pd.DataFrame): The DataFrame to work with.
        columns_name (list): A list of columns to impute with default values.

    Returns:
        Nothing, it transforms the column inplace.
    """
    
    # 
    for column_to_fill in columns_names:
        
        # this is a mask of null values to be imputed
        null_mask = dataFrame[column_to_fill].isna()

        # This fork statement is only to evaluate the column dtype.

        if dataFrame[column_to_fill].dtype == float or dataFrame[column_to_fill].dtype == int: # If it is numeric either int or float: impute.
            dataFrame.loc[null_mask, column_to_fill] = 0
            
        elif pd.core.dtypes.common.is_datetime_or_timedelta_dtype(dataFrame[column_to_fill]): # If it is a pandas Timestamp object, then impute.
            dataFrame.loc[null_mask, column_to_fill] = pd.Timestamp('1900-01-01')

In [39]:
# Lets call our defaults filler function
columns_with_nulls = ['revenue', 'budget', 'release_date']

defaults_filler(df_copy, columns_with_nulls)

In [40]:
df_copy.isna().sum()

belongs_to_collection    40972
budget                       0
genres                       0
id                           0
original_language           11
overview                   959
popularity                   5
production_companies         3
production_countries         3
release_date                 0
revenue                      0
runtime                    263
spoken_languages             6
status                      87
tagline                  25055
title                        6
vote_average                 6
vote_count                   6
dtype: int64

### Creating a "year"

This is also a simple since pandas series objects offers functionalities to pd.Timestamp objects, such as accesors in order to extract the information that we need from our series

In [42]:
# Checking what pd.Series.dt accesor could provide
df_copy['release_date'].dt.year

0        1995
1        1995
2        1995
3        1995
4        1995
         ... 
45461    1900
45462    2011
45463    2003
45464    1917
45465    2017
Name: release_date, Length: 45466, dtype: int32

In [43]:
# Creating new column
df_copy["release_year"] = df_copy.release_date.dt.year

Let's have a look at our data frame how it looks like so far..

In [44]:
df_copy.head(1).T 

0
belongs_to_collection  {'id': 10194, 'name': 'Toy Story Collection', ...
budget                                                          30000000
genres                 [{'id': 16, 'name': 'Animation'}, {'id': 35, '...
id                                                                   862
original_language                                                     en
overview               Led by Woody, Andy's toys live happily in his ...
popularity                                                     21.946943
production_companies      [{'name': 'Pixar Animation Studios', 'id': 3}]
production_countries   [{'iso_3166_1': 'US', 'name': 'United States o...
release_date                                         1995-10-30 00:00:00
revenue                                                      373554033.0
runtime                                                             81.0
spoken_languages                [{'iso_639_1': 'en', 'name': 'English'}]
status                                                          Released
tagline                                                              NaN
title                                                          Toy Story
vote_average                                                         7.7
vote_count                                                        5415.0
release_year                                                        1995

### Data Types Consistency
Sometimes, there could be some unexpected data in a field, either a string datatype in a numeric field or a numeric dtype in a string field. It is important to check datatype consistency on each field. And the bellow ad-hoc function will help us to do that a bit more easy

In [206]:
def dtype_checker(dataFrame: pd.DataFrame, column: str, data_type) -> list:
     
    """
    Returns an array of indexes of rows with a different data type in the specified column.

    Parameters:
        dataFrame (pd.DataFrame): The DataFrame to check.
        column (str): The name of the column to check for data type.
        data_type: The expected data type for the values in the column.

    Returns:
        list: An array of indexes of rows where the data type in the specified column is different from the expected data type.
    """

    invalid_dtype_rows = []


    for idx,row in enumerate(dataFrame[column]):
        if type(row) == data_type:
            pass
        else:
            invalid_dtype_rows.append(idx)
        
    return invalid_dtype_rows



In [20]:
type(df_copy['title'][0])

str

In [21]:
df_copy.loc[dtype_checker(df_copy, "title", str), "title"]

2079           54
2198         2010
4335         1969
5338         1776
6509           10
           ...   
43535         305
44437         977
44627    07:19:00
44956    02:22:00
45058           1
Name: title, Length: 88, dtype: object

In [22]:
df_copy.loc[dtype_checker(df_copy, "title", str), "title"].index

Int64Index([ 2079,  2198,  4335,  5338,  6509,  6952,  8753,  9211,  9377,
             9506, 10403, 10923, 10948, 11189, 11662, 11917, 12204, 12321,
            12508, 12972, 13345, 13849, 14117, 14416, 14832, 15569, 15617,
            16226, 17016, 17105, 17180, 18026, 18116, 19421, 19729, 19730,
            19956, 20648, 20759, 20882, 21078, 22837, 22987, 22988, 23756,
            23856, 24062, 24144, 24238, 24524, 25458, 25459, 28293, 29160,
            29366, 29502, 29503, 29765, 30567, 31108, 32714, 33056, 33383,
            33631, 33931, 34622, 34829, 35586, 35587, 37062, 37381, 37965,
            39013, 39671, 40518, 40542, 40971, 40985, 42502, 43048, 43199,
            43249, 43293, 43535, 44437, 44627, 44956, 45058],
           dtype='int64')

In [23]:
import datetime

datetime_index = []

for index_s in df_copy.loc[dtype_checker(df_copy, "title", str), "title"].index:

    if  isinstance(df_copy.loc[index_s, "title"], datetime.time):
        datetime_index.append(index_s)



In [24]:
datetime_index

[9377,
 9506,
 11189,
 13345,
 15569,
 17180,
 20648,
 20882,
 28293,
 29160,
 34829,
 43249,
 43293,
 44627,
 44956]

In [25]:
df_copy.loc[datetime_index, "title"] = "No title"

In [26]:
df_copy.loc[datetime_index, "title"]

9377     No title
9506     No title
11189    No title
13345    No title
15569    No title
17180    No title
20648    No title
20882    No title
28293    No title
29160    No title
34829    No title
43249    No title
43293    No title
44627    No title
44956    No title
Name: title, dtype: object

In [27]:
df_copy["title"] = df_copy["title"].astype(str)

In [28]:
df_copy["title"]

0                          Toy Story
1                            Jumanji
2                   Grumpier Old Men
3                  Waiting to Exhale
4        Father of the Bride Part II
                    ...             
45461                         Subdue
45462            Century of Birthing
45463                       Betrayal
45464               Satan Triumphant
45465                       Queerama
Name: title, Length: 45466, dtype: object

In [29]:
diff_dtype_mask = dtype_checker(df_copy, "budget", int)
df_copy.loc[diff_dtype_mask, "budget"] = 0

In [30]:
df_copy.loc[4,"revenue"], df_copy.loc[4,"budget"]

(76578911.0, 0)

In [31]:
df_copy["return_on_investment"] = df_copy["revenue"].div(df_copy["budget"].astype(float)).fillna(0).replace([np.inf, -np.inf], 0)

In [32]:
df_copy.head(2).T

0  \
belongs_to_collection  {'id': 10194, 'name': 'Toy Story Collection', ...   
budget                                                          30000000   
genres                 [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
id                                                                   862   
original_language                                                     en   
overview               Led by Woody, Andy's toys live happily in his ...   
popularity                                                     21.946943   
production_companies      [{'name': 'Pixar Animation Studios', 'id': 3}]   
production_countries   [{'iso_3166_1': 'US', 'name': 'United States o...   
release_date                                         1995-10-30 00:00:00   
revenue                                                      373554033.0   
runtime                                                             81.0   
spoken_languages                [{'iso_639_1': 'en', 'name': 'English'}]   
status                                                          Released   
tagline                                                              NaN   
title                                                          Toy Story   
vote_average                                                         7.7   
vote_count                                                        5415.0   
release_year                                                        1995   
return_on_investment                                           12.451801   

                                                                       1  
belongs_to_collection                                                NaN  
budget                                                          65000000  
genres                 [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...  
id                                                                  8844  
original_language                                                     en  
overview               When siblings Judy and Peter discover an encha...  
popularity                                                     17.015539  
production_companies   [{'name': 'TriStar Pictures', 'id': 559}, {'na...  
production_countries   [{'iso_3166_1': 'US', 'name': 'United States o...  
release_date                                         1995-12-15 00:00:00  
revenue                                                      262797249.0  
runtime                                                            104.0  
spoken_languages       [{'iso_639_1': 'en', 'name': 'English'}, {'iso...  
status                                                          Released  
tagline                        Roll the dice and unleash the excitement!  
title                                                            Jumanji  
vote_average                                                         6.9  
vote_count                                                        2413.0  
release_year                                                        1995  
return_on_investment                                            4.043035

In [33]:
def safe_literal_eval(x):
    try:
        return ast.literal_eval(x)
    except (ValueError, SyntaxError):
        return [{}]

In [34]:
nested_data_columns

['belongs_to_collection',
 'genres',
 'production_companies',
 'production_countries',
 'spoken_languages']

In [35]:
for column in nested_data_columns:
    df_copy[column] = df_copy[column].apply(safe_literal_eval)

In [36]:
df_copy.loc[:,nested_data_columns].isna().sum()

belongs_to_collection    0
genres                   0
production_companies     0
production_countries     0
spoken_languages         0
dtype: int64

In [37]:
df_copy.dtypes

belongs_to_collection            object
budget                           object
genres                           object
id                               object
original_language                object
overview                         object
popularity                       object
production_companies             object
production_countries             object
release_date             datetime64[ns]
revenue                         float64
runtime                         float64
spoken_languages                 object
status                           object
tagline                          object
title                            object
vote_average                    float64
vote_count                      float64
release_year                      int64
return_on_investment            float64
dtype: object

In [38]:
df_copy["release_date"] = df_copy["release_date"].apply(lambda x: x.strftime("%Y-%m-%d"))

In [39]:
df_copy.loc[0,"release_date"]

'1995-10-30'

In [155]:
df_copy

belongs_to_collection    budget  \
0      {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1                                                   [{}]  65000000   
2      {'id': 119050, 'name': 'Grumpy Old Men Collect...         0   
3                                                   [{}]  16000000   
4      {'id': 96871, 'name': 'Father of the Bride Col...         0   
...                                                  ...       ...   
45461                                               [{}]         0   
45462                                               [{}]         0   
45463                                               [{}]         0   
45464                                               [{}]         0   
45465                                               [{}]         0   

                                                  genres      id  \
0      [{'id': 16, 'name': 'Animation'}, {'id': 35, '...     862   
1      [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...    8844   
2      [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...   15602   
3      [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   31357   
4                         [{'id': 35, 'name': 'Comedy'}]   11862   
...                                                  ...     ...   
45461  [{'id': 18, 'name': 'Drama'}, {'id': 10751, 'n...  439050   
45462                      [{'id': 18, 'name': 'Drama'}]  111109   
45463  [{'id': 28, 'name': 'Action'}, {'id': 18, 'nam...   67758   
45464                                                 []  227506   
45465                                                 []  461257   

      original_language                                           overview  \
0                    en  Led by Woody, Andy's toys live happily in his ...   
1                    en  When siblings Judy and Peter discover an encha...   
2                    en  A family wedding reignites the ancient feud be...   
3                    en  Cheated on, mistreated and stepped on, the wom...   
4                    en  Just when George Banks has recovered from his ...   
...                 ...                                                ...   
45461                fa        Rising and falling between a man and woman.   
45462                tl  An artist struggles to finish his work while a...   
45463                en  When one of her hits goes wrong, a professiona...   
45464                en  In a small town live two brothers, one a minis...   
45465                en  50 years after decriminalisation of homosexual...   

      popularity                               production_companies  \
0      21.946943     [{'name': 'Pixar Animation Studios', 'id': 3}]   
1      17.015539  [{'name': 'TriStar Pictures', 'id': 559}, {'na...   
2        11.7129  [{'name': 'Warner Bros.', 'id': 6194}, {'name'...   
3       3.859495  [{'name': 'Twentieth Century Fox Film Corporat...   
4       8.387519  [{'name': 'Sandollar Productions', 'id': 5842}...   
...          ...                                                ...   
45461   0.072051                                                 []   
45462   0.178241             [{'name': 'Sine Olivia', 'id': 19653}]   
45463   0.903007  [{'name': 'American World Pictures', 'id': 6165}]   
45464   0.003503               [{'name': 'Yermoliev', 'id': 88753}]   
45465   0.163015                                                 []   

                                    production_countries release_date  \
0      [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   
1      [{'iso_3166_1': 'US', 'name': 'United States o...   1995-12-15   
2      [{'iso_3166_1': 'US', 'name': 'United States o...   1995-12-22   
3      [{'iso_3166_1': 'US', 'name': 'United States o...   1995-12-22   
4      [{'iso_3166_1': 'US', 'name': 'United States o...   1995-02-10   
...                                                  ...          ...   
45461             [{'iso_3166_1': 'IR', 'name': 'Iran'}]   1900-01-01   
454

# Converting Data Frame to a json object to upload it to MontoAtlas

In [40]:
df_json = df_copy.to_dict(orient="records")

### Setting up connection to Atlas Cloud Data Base

In [91]:
from urllib.parse import quote_plus
from pymongo.mongo_client import MongoClient
from pymongo.server_api import ServerApi

user = "someone_from_93"
password = "rg550dx93"

uri = "mongodb+srv://" + user  +":" + password + "@cluster0.muda7ep.mongodb.net/?retryWrites=true&w=majority"
# Create a new client and connect to the server
client_atlas = MongoClient(uri, server_api=ServerApi('1'))
# Send a ping to confirm a successful connection
try:
    client_atlas.admin.command('ping')
    print("Pinged your deployment. You successfully connected to MongoDB!")
except Exception as e:
    print(e)

Pinged your deployment. You successfully connected to MongoDB!


In [103]:
mongAtlas_db = client_atlas.pi_henry

In [105]:
mongAtlas_db.movies.insert_many(df_json)

In [134]:
doc_demo = mongAtlas_db.movies.find_one()

In [129]:
mongAtlas_db.movies.distinct("genres")

[{'id': 12, 'name': 'Adventure'},
 {'id': 14, 'name': 'Fantasy'},
 {'id': 16, 'name': 'Animation'},
 {'id': 18, 'name': 'Drama'},
 {'id': 27, 'name': 'Horror'},
 {'id': 28, 'name': 'Action'},
 {'id': 35, 'name': 'Comedy'},
 {'id': 36, 'name': 'History'},
 {'id': 37, 'name': 'Western'},
 {'id': 53, 'name': 'Thriller'},
 {'id': 80, 'name': 'Crime'},
 {'id': 99, 'name': 'Documentary'},
 {'id': 878, 'name': 'Science Fiction'},
 {'id': 9648, 'name': 'Mystery'},
 {'id': 10402, 'name': 'Music'},
 {'id': 10749, 'name': 'Romance'},
 {'id': 10751, 'name': 'Family'},
 {'id': 10752, 'name': 'War'},
 {'id': 10769, 'name': 'Foreign'},
 {'id': 10770, 'name': 'TV Movie'},
 {'name': 'Aniplex', 'id': 2883},
 {'name': 'BROSTA TV', 'id': 7760},
 {'name': 'Carousel Productions', 'id': 11176},
 {'name': 'GoHands', 'id': 7759},
 {'name': 'Mardock Scramble Production Committee', 'id': 7761},
 {'name': 'Odyssey Media', 'id': 17161},
 {'name': 'Pulser Productions', 'id': 18012},
 {'name': 'Rogue State', 'id': 1

In [162]:
list(mongAtlas_db.movies.find({"belongs_to_collection.0": {"$exists": False}}))

[{'_id': ObjectId('649785c95bae6ab81f02516f'),
  'belongs_to_collection': {'id': 10194,
   'name': 'Toy Story Collection',
   'poster_path': '/7G9915LfUQ2lVfwMEEhDsn3kT4B.jpg',
   'backdrop_path': '/9FBwqcd9IRruEDUrTdcaafOMKUq.jpg'},
  'budget': 30000000,
  'genres': [{'id': 16, 'name': 'Animation'},
   {'id': 35, 'name': 'Comedy'},
   {'id': 10751, 'name': 'Family'}],
  'id': 862,
  'original_language': 'en',
  'overview': "Led by Woody, Andy's toys live happily in his room until Andy's birthday brings Buzz Lightyear onto the scene. Afraid of losing his place in Andy's heart, Woody plots against Buzz. But when circumstances separate Buzz and Woody from their owner, the duo eventually learns to put aside their differences.",
  'popularity': 21.946943,
  'production_companies': [{'name': 'Pixar Animation Studios', 'id': 3}],
  'production_countries': [{'iso_3166_1': 'US',
    'name': 'United States of America'}],
  'release_date': '1995-10-30',
  'revenue': 373554033.0,
  'runtime': 81.

In [175]:
mongAtlas_db.movies.find_one({"popularity": {"$lt": 2.0}})

{'_id': ObjectId('649785c95bae6ab81f025188'),
 'belongs_to_collection': [{}],
 'budget': 0,
 'genres': [{'id': 18, 'name': 'Drama'}],
 'id': 16420,
 'original_language': 'en',
 'overview': 'The evil Iago pretends to be friend of Othello in order to manipulate him to serve his own end in the film version of this Shakespeare classic.',
 'popularity': 1.845899,
 'production_companies': [{'name': 'Columbia Pictures', 'id': 5},
  {'name': 'Castle Rock Entertainment', 'id': 97}],
 'production_countries': [{'iso_3166_1': 'IT', 'name': 'Italy'}],
 'release_date': '1995-12-15',
 'revenue': 0.0,
 'runtime': 123.0,
 'spoken_languages': [{'iso_639_1': 'en', 'name': 'English'}],
 'status': 'Released',
 'tagline': 'Envy, greed, jealousy and love.',
 'title': 'Othello',
 'vote_average': 7.0,
 'vote_count': 33.0,
 'release_year': 1995,
 'return_on_investment': 0.0}

In [181]:
mongAtlas_db.movies.find({"popularity": {"$lt": 2.0}})

# Credit File Wrangling

In [264]:
df_credit = pd.read_csv("Data\credits.csv")

In [265]:
df_credit_copy = df_credit.copy()

In [266]:
df_credit_copy.head()

cast  \
0  [{'cast_id': 14, 'character': 'Woody (voice)',...   
1  [{'cast_id': 1, 'character': 'Alan Parrish', '...   
2  [{'cast_id': 2, 'character': 'Max Goldman', 'c...   
3  [{'cast_id': 1, 'character': "Savannah 'Vannah...   
4  [{'cast_id': 1, 'character': 'George Banks', '...   

                                                crew     id  
0  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...    862  
1  [{'credit_id': '52fe44bfc3a36847f80a7cd1', 'de...   8844  
2  [{'credit_id': '52fe466a9251416c75077a89', 'de...  15602  
3  [{'credit_id': '52fe44779251416c91011acb', 'de...  31357  
4  [{'credit_id': '52fe44959251416c75039ed7', 'de...  11862

In [267]:
df_credit_copy.dtypes

cast    object
crew    object
id       int64
dtype: object

In [268]:
df_credit_copy.isna().sum()

cast    0
crew    0
id      0
dtype: int64

In [269]:
type(df_credit_copy["cast"][0])

str

In [270]:
df_credit_copy.columns

Index(['cast', 'crew', 'id'], dtype='object')

In [271]:
columns_to_literal = ['cast', 'crew']
for column in columns_to_literal:
    df_credit_copy[column] = df_credit_copy[column].apply(safe_literal_eval)

In [272]:
assert type(df_credit_copy["cast"][0]) == list

In [310]:
dtype_checker(df_credit_copy, column="id", data_type=int)

[]

In [311]:
dtype_checker(df_credit_copy, "crew", list)

[]

In [312]:
dtype_checker(df_credit_copy, "cast", list)

[]

In [331]:
range(df_credit_copy['crew'].size -1)

range(0, 45475)

In [389]:
df_credit_copy['crew'][0][0].get('job')

'Director'

In [392]:
filtered_data = df_credit_copy["crew"].apply(lambda movie_crew: [member for member in movie_crew if member.get('job') == 'Director'])

In [405]:
colab_count = []
for idx, value in enumerate(filtered_data):
    if len(value) > 6:
        colab_count.append(idx)


In [409]:
df_credit_copy.loc[colab_count, "crew"]

1237     [{'credit_id': '52fe4272c3a36847f801f2e7', 'de...
1909     [{'credit_id': '52fe438cc3a36847f805ca73', 'de...
3042     [{'credit_id': '59078d1c925141643300101e', 'de...
7437     [{'credit_id': '52fe4322c3a36847f803cfdd', 'de...
7768     [{'credit_id': '56727e78c3a368070e001c51', 'de...
                               ...                        
42281    [{'credit_id': '57fb8393925141434b008b9f', 'de...
43200    [{'credit_id': '56731cd9c3a368070c002fbd', 'de...
43821    [{'credit_id': '581ae882c3a3683db800184c', 'de...
45120    [{'credit_id': '52fe48f8c3a368484e113ea9', 'de...
45195    [{'credit_id': '55c8cff7c3a3686b5f000b3d', 'de...
Name: crew, Length: 62, dtype: object

In [414]:
df_credit_copy.loc[1237]

cast    [{'cast_id': 14, 'character': 'Narrator - Narr...
crew    [{'credit_id': '52fe4272c3a36847f801f2e7', 'de...
id                                                    756
Name: 1237, dtype: object

In [415]:
mongAtlas_db.movies.find_one({"id": 756})

{'_id': ObjectId('649785c95bae6ab81f025644'),
 'belongs_to_collection': {'id': 55427,
  'name': 'Fantasia Collection',
  'poster_path': '/qHpXVQVhSOXwFNFCfKfdTnuyrXl.jpg',
  'backdrop_path': '/7YanwpylLB3yzhwzf11W1tYpcQF.jpg'},
 'budget': 2280000,
 'genres': [{'id': 16, 'name': 'Animation'},
  {'id': 10751, 'name': 'Family'},
  {'id': 10402, 'name': 'Music'}],
 'id': 756,
 'original_language': 'en',
 'overview': "Walt Disney's timeless masterpiece is an extravaganza of sight and sound! See the music come to life, hear the pictures burst into song and experience the excitement that is Fantasia over and over again.",
 'popularity': 8.03796,
 'production_companies': [{'name': 'Walt Disney Pictures', 'id': 2}],
 'production_countries': [{'iso_3166_1': 'US',
   'name': 'United States of America'}],
 'release_date': '1940-11-13',
 'revenue': 83320000.0,
 'runtime': 124.0,
 'spoken_languages': [{'iso_639_1': 'en', 'name': 'English'}],
 'status': 'Released',
 'tagline': "The most sensational s

In [418]:
df_credit_copy['crew'] = df_credit_copy["crew"].apply(lambda movie_crew: [member for member in movie_crew if member.get('job') == 'Director'])

In [419]:
df_credit_copy['crew'][0]

[{'credit_id': '52fe4284c3a36847f8024f49',
  'department': 'Directing',
  'gender': 2,
  'id': 7879,
  'job': 'Director',
  'name': 'John Lasseter',
  'profile_path': '/7EdqiNbr4FRjIhKHyPPdFfEEEFG.jpg'}]

In [420]:
credits_dict = df_credit_copy.to_dict("records")

In [424]:
credits_dict

[{'cast': [{'cast_id': 14,
    'character': 'Woody (voice)',
    'credit_id': '52fe4284c3a36847f8024f95',
    'gender': 2,
    'id': 31,
    'name': 'Tom Hanks',
    'order': 0,
    'profile_path': '/pQFoyx7rp09CJTAb932F2g8Nlho.jpg'},
   {'cast_id': 15,
    'character': 'Buzz Lightyear (voice)',
    'credit_id': '52fe4284c3a36847f8024f99',
    'gender': 2,
    'id': 12898,
    'name': 'Tim Allen',
    'order': 1,
    'profile_path': '/uX2xVf6pMmPepxnvFWyBtjexzgY.jpg'},
   {'cast_id': 16,
    'character': 'Mr. Potato Head (voice)',
    'credit_id': '52fe4284c3a36847f8024f9d',
    'gender': 2,
    'id': 7167,
    'name': 'Don Rickles',
    'order': 2,
    'profile_path': '/h5BcaDMPRVLHLDzbQavec4xfSdt.jpg'},
   {'cast_id': 17,
    'character': 'Slinky Dog (voice)',
    'credit_id': '52fe4284c3a36847f8024fa1',
    'gender': 2,
    'id': 12899,
    'name': 'Jim Varney',
    'order': 3,
    'profile_path': '/eIo2jVVXYgjDtaHoF19Ll9vtW7h.jpg'},
   {'cast_id': 18,
    'character': 'Rex (voice)'

In [425]:
mongAtlas_db.credits.insert_many(credits_dict)